# How can we control the increasing number of accidents in New York?

In [1]:
//Download needed libraries
import $ivy.`org.apache.spark::spark-sql:2.4.0`
import $ivy.`org.jsoup:jsoup:1.12.1`
import $ivy.`org.plotly-scala::plotly-almond:0.7.2`

Downloaded https://repo1.maven.org/maven2/org/apache/spark/spark-kvstore_2.12/2.4.0/spark-kvstore_2.12-2.4.0-sources.jar
Downloaded https://repo1.maven.org/maven2/org/apache/spark/spark-unsafe_2.12/2.4.0/spark-unsafe_2.12-2.4.0-sources.jar
Downloaded https://repo1.maven.org/maven2/io/dropwizard/metrics/metrics-core/3.1.5/metrics-core-3.1.5-sources.jar
Downloaded https://repo1.maven.org/maven2/com/ning/compress-lzf/1.0.3/compress-lzf-1.0.3-sources.jar
Downloaded https://repo1.maven.org/maven2/org/lz4/lz4-java/1.4.0/lz4-java-1.4.0-sources.jar
Downloaded https://repo1.maven.org/maven2/org/roaringbitmap/RoaringBitmap/0.5.11/RoaringBitmap-0.5.11-sources.jar
Downloaded https://repo1.maven.org/maven2/xmlenc/xmlenc/0.52/xmlenc-0.52-sources.jar
Downloaded https://repo1.maven.org/maven2/xerces/xercesImpl/2.9.1/xercesImpl-2.9.1-sources.jar
Downloaded https://repo1.maven.org/maven2/org/json4s/json4s-scalap_2.12/3.5.3/json4s-scalap_2.12-3.5.3-sources.jar
Downloaded https://repo1.maven.org/maven2/or

Downloaded https://repo1.maven.org/maven2/org/glassfish/jersey/core/jersey-common/2.22.2/jersey-common-2.22.2-sources.jar
Downloaded https://repo1.maven.org/maven2/javax/servlet/javax.servlet-api/3.1.0/javax.servlet-api-3.1.0-sources.jar
Downloaded https://repo1.maven.org/maven2/org/apache/spark/spark-network-shuffle_2.12/2.4.0/spark-network-shuffle_2.12-2.4.0-sources.jar
Downloaded https://repo1.maven.org/maven2/org/scala-lang/scala-reflect/2.12.1/scala-reflect-2.12.1-sources.jar
Downloaded https://repo1.maven.org/maven2/org/json4s/json4s-jackson_2.12/3.5.3/json4s-jackson_2.12-3.5.3-sources.jar
Downloaded https://repo1.maven.org/maven2/org/apache/commons/commons-lang3/3.5/commons-lang3-3.5-sources.jar
Downloaded https://repo1.maven.org/maven2/net/razorvine/pyrolite/4.13/pyrolite-4.13-sources.jar
Downloaded https://repo1.maven.org/maven2/org/glassfish/hk2/external/aopalliance-repackaged/2.4.0-b34/aopalliance-repackaged-2.4.0-b34-sources.jar
Downloaded https://repo1.maven.org/maven2/io/

Downloaded https://repo1.maven.org/maven2/sh/almond/ammonite-spark_2.12/0.7.2/ammonite-spark_2.12-0.7.2-sources.jar
Downloaded https://repo1.maven.org/maven2/org/apache/spark/spark-sql_2.12/2.4.0/spark-sql_2.12-2.4.0-sources.jar
Downloaded https://repo1.maven.org/maven2/org/codehaus/janino/janino/3.0.9/janino-3.0.9-sources.jar
Downloaded https://repo1.maven.org/maven2/org/scala-lang/modules/scala-parser-combinators_2.12/1.1.0/scala-parser-combinators_2.12-1.1.0-sources.jar
Downloaded https://repo1.maven.org/maven2/joda-time/joda-time/2.9.9/joda-time-2.9.9-sources.jar
Downloaded https://repo1.maven.org/maven2/sh/almond/almond-spark_2.12/0.9.1/almond-spark_2.12-0.9.1-sources.jar
Downloaded https://repo1.maven.org/maven2/org/apache/arrow/arrow-format/0.10.0/arrow-format-0.10.0-sources.jar
Downloaded https://repo1.maven.org/maven2/org/eclipse/jetty/jetty-http/9.4.20.v20190813/jetty-http-9.4.20.v20190813-sources.jar
Downloaded https://repo1.maven.org/maven2/org/apache/spark/spark-catalyst_2

import $ivy.$                                  

import $ivy.$                       

import $ivy.$                                      

In [2]:
//Import libraries
import java.io._
import org.apache.spark.sql._
import org.jsoup._

import plotly._
import plotly.element._
import plotly.layout._
import plotly.Almond._
import org.apache.spark.sql.functions._

import java.io._

import org.apache.spark.sql._

import org.jsoup._


import plotly._

import plotly.element._

import plotly.layout._

import plotly.Almond._

import org.apache.spark.sql.functions._

In [3]:
//Deactivate logger for clearer outputs
import org.apache.log4j.{Level, Logger}
Logger.getLogger("org").setLevel(Level.OFF)

import org.apache.log4j.{Level, Logger}


In [4]:
val spark = {
  NotebookSparkSession.builder()
    .master("local[*]")
    .getOrCreate()
}
import spark.implicits._

Loading spark-stubs


Downloaded https://repo1.maven.org/maven2/sh/almond/spark-stubs_24_2.12/0.7.2/spark-stubs_24_2.12-0.7.2.pom
Downloaded https://repo1.maven.org/maven2/sh/almond/spark-stubs_24_2.12/0.7.2/spark-stubs_24_2.12-0.7.2-sources.jar
Downloaded https://repo1.maven.org/maven2/sh/almond/spark-stubs_24_2.12/0.7.2/spark-stubs_24_2.12-0.7.2.jar


Getting spark JARs
Creating SparkSession


Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties


Spark UI

spark: SparkSession = org.apache.spark.sql.SparkSession@2fb9a3bd
import spark.implicits._

## Introduction

**Business Context.** The city of New York has seen a rise in the number of accidents on the roads in the city. They would like to know if the number of accidents have increased in the last few weeks. For all the reported accidents, they have collected details for each accident and have been maintaining records for the past year and a half (from January 2018 to August 2019). 

The city has contracted you to build visualizations that would help them identify patterns in accidents, which would help them take preventive actions to reduce the number of accidents in the future. They have certain parameters like borough, time of day, reason for accident, etc. Which they care about and which they would like to get specific information on.

**Business Problem.** Your task is to format the given data and provide visualizations that would answer the specific questions the client has, which are mentioned below.

**Analytical Context.** You are given a CSV file containing details about each accident like date, time, location of the accident, reason for the accident, types of vehicles involved, injury and death count, etc. The delimiter in the given CSV file is `;` instead of the default `,`. You will be performing the following tasks on the data:

1. Extract data from Wikipedia
2. Read, transform, and prepare data for visualization
3. Perform analytics and construct visualizations of the data to identify patterns in the dataset
        
The client has a specific set of questions they would like to get answers to. You will need to provide visualizations to accompany these:

1. How have the number of accidents fluctuated over the past year and a half? Have they increased over the time?
2. For any particular day, during which hours are accidents most likely to occur?
3. Are there more accidents on weekdays than weekends?
4. What are the accidents count-to-area ratio per borough? Which boroughs have disproportionately large numbers of accidents for their size?
5. For each borough, during which hours are accidents most likely to occur?
6. What are the top 5 causes of accidents in the city? 
7. What types of vehicles are most involved in accidents per borough?
8. What types of vehicles are most involved in deaths?


## Fetch borough data from Wikipedia

The client has requested analysis of the accidents-to-area ratio for boroughs. You will need to fetch the area of each borough from the Wikipedia page: https://en.wikipedia.org/wiki/Boroughs_of_New_York_City.

Since we are fetching this resource from an external page, you should instead fetch the HTML document and store the results locally in a JSON file, so that you can parse it later when you need it. Create a folder named `data` and store the file inside it.

Insert **answer** below:

In [ ]:
//Scrapy into a website
def scrapy_url(url:String, filePath:String =null ): nodes.Document = {
    val doc = Jsoup.connect(url).get()
    if(filePath != null){
        new PrintWriter(filePath){
            write(doc.toString);
            close
        }
    }
    
    
    return doc
}

In [ ]:
val url = "https://en.wikipedia.org/wiki/Boroughs_of_New_York_City"
val html = scrapy_url(url, "docs/wikipedia.html")

In [ ]:
html.getElementsByTag("th")

For later usage, let's store the borough data into a JSON file in the already created `data` folder:

## Overview of the data

Now that we've stored the borough data in a JSON file, we can re-open it and use it whenever we wish. We can use the `read_json()` function in `pandas` to do that:

In [5]:
val df: DataFrame = spark
  .read
  .format("csv")
  .option("delimiter", ";")
  .option("header", true)
  .option("inferSchema", true)
  .load("docs/accidents.csv")

load at cmd4.sc:7

1 / 1

load at cmd4.sc:7

12 / 12

df: DataFrame = [DATE: string, TIME: string ... 22 more fields]

In [6]:
df.printSchema()

root
 |-- DATE: string (nullable = true)
 |-- TIME: string (nullable = true)
 |-- BOROUGH: string (nullable = true)
 |-- ZIP CODE: double (nullable = true)
 |-- LATITUDE: double (nullable = true)
 |-- LONGITUDE: double (nullable = true)
 |-- ON STREET NAME: string (nullable = true)
 |-- NUMBER OF PEDESTRIANS INJURED: integer (nullable = true)
 |-- NUMBER OF PEDESTRIANS KILLED: integer (nullable = true)
 |-- NUMBER OF CYCLIST INJURED: integer (nullable = true)
 |-- NUMBER OF CYCLIST KILLED: integer (nullable = true)
 |-- NUMBER OF MOTORIST INJURED: integer (nullable = true)
 |-- NUMBER OF MOTORIST KILLED: integer (nullable = true)
 |-- CONTRIBUTING FACTOR VEHICLE 1: string (nullable = true)
 |-- CONTRIBUTING FACTOR VEHICLE 2: string (nullable = true)
 |-- CONTRIBUTING FACTOR VEHICLE 3: string (nullable = true)
 |-- CONTRIBUTING FACTOR VEHICLE 4: string (nullable = true)
 |-- CONTRIBUTING FACTOR VEHICLE 5: string (nullable = true)
 |-- COLLISION_ID: integer (nullable = true)
 |-- VEHICLE

In [7]:
val df2 = df.withColumn("MONTH", col("DATE").substr(0,2))

df2: DataFrame = [DATE: string, TIME: string ... 23 more fields]

In [8]:
val (x, y) = df2.collect.map(r=>(r(24).toString, r(7).toString.toInt)).toList.unzip

collect at cmd7.sc:1

10 / 10

x: List[String] = List(
  "09",
  "09",
  "08",
  "09",
  "08",
  "08",
  "08",
  "09",
  "09",
  "08",
  "08",
  "08",
  "08",
  "09",
  "09",
  "09",
  "09",
  "09",
  "09",
  "08",
  "08",
  "09",
  "09",
  "09",
  "08",
  "08",
  "08",
  "08",
  "08",
  "09",
  "09",
  "09",
  "09",
  "08",
  "09",
  "08",
  "08",
  "08",
...
y: List[Int] = List(
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
...

In [9]:
val plot = Seq(
    Bar(
    x, y, name="Test"))

plot: Seq[Bar] = List(
  (
    Strings(
      List(
        "09",
        "09",
        "08",
        "09",
        "08",
        "08",
        "08",
        "09",
        "09",
        "08",
        "08",
        "08",
        "08",
        "09",
        "09",
        "09",
        "09",
        "09",
        "09",
        "08",
        "08",
        "09",
        "09",
        "09",
        "08",
        "08",
        "08",
        "08",
        "08",
        "09",
        "09",
        "09",
        "09",
        "08",
        "09",
...

In [10]:
plot.plot(
title="NUMBER OF PEDESTRIANS INJURIED THROUGH A YEAR")

res9: String = "plot-cdb26c39-0062-4654-a9fe-f4a1da30c743"

Let's go through the columns present in the dataframe:

We have the following columns

1. **Borough**: The borough in which the accident occured
2. **COLLISION_ID**: A unique identifier for this collision
3. **CONTRIBUTING FACTOR VEHICLE (1, 2, 3, 4, 5)**: Reasons for the accident
4. **CROSS STREET NAME**: Nearest cross street to the place of accidents
5. **DATE**: Date of the accident
6. **TIME**: Time of accident
7. **DATETIME**: The column we previously created with the combination of date and time
8. **LATITUDE**: Latitude of the accident
9. **LONGITUDE**: Longitude of the accident
10. **NUMBER OF (CYCLIST, MOTORIST, PEDESTRIANS) INJURED**: Category wise injury
11. **NUMBER OF (CYCLIST, MOTORIST, PEDESTRIANS) KILLED**: Category wise death
12. **ON STREET NAME**: Street where the accident occured
13. **TOTAL INJURED**: Total injury from the accident
14. **TOTAL KILLED**: Total casualties in the accident
15. **VEHICLE TYPE CODE (1, 2, 3, 4, 5)**: Types of vehicles involved in the accident
16. **ZIP CODE**: zip code of the accident location

Let's go ahead and answer each of the client's questions.

## Answering the client's questions

### Part 1: Accidents over time

Group the available data on a monthly basis and generate a line plot of accidents over time. Has the number of accidents increased over the past year and a half?

Insert **answer** below:

**Type your answer to the question in this cell**

### Part 2: Accident hotspots in a day

How does the number of accidents vary throughout a single day? Create a new column `HOUR` based on the data from the `DATETIME` column, then plot a bar graph of the distribution per hour throughout the day.

Insert **answer** below:

**Type your answer to the question in this cell**

### Part 3: Accidents by weekday

How does the number of accidents vary throughout a single week? Plot a bar graph based on the accidents count by day of the week.

Insert **answer** below:

**Type your answer to the question in this cell**

### Part 4: Borough analysis

Plot a bar graph of the total number of accidents in each borough, as well as one of the accidents per square kilometer per borough. What can you conclude?

Insert **answer** below:

**Type your answer to the question in this cell**

We have now got the keys to match in the dictionary and the dataframe. The difference in case can be handled by making the mapping action case-insensitive. This can be done by either converting the dictionary keys to uppercase, or the dataframe data to lowercase.

Let's do that and plot `accidents_per_sq_km`, which is the accidents-to-area ratio:

**Type your answer to the question in this cell**

### Part 5: Borough hourly analysis

Which hours have the most accidents for each borough? Plot a bar graph for each borough showing the number of accidents for each hour of the day.

Insert **answer** below:

**Is the number of accidents higher at different times in different boroughs? Should we concentrate at different times for each borough?**

**Type your answer to the question in this cell**

### Part 6: Cause of accidents

What factors cause the most accidents?

Insert **answer** below:

**Type your answer to the question in this cell**

### Part 7: Boroughs and vehicle types

Which vehicle types are most involved in accidents per borough?

Insert **answer** below:

**Type your answer to the question in this cell**

### Part 8: Death counts by vehicle type

Calculate the number of deaths by vehicle and plot a bar chart for the top 5 vehicles. Which vehicles are most often involved in deaths, and by how much more than the others?

Insert **answer** below:

**Type your answer to the question in this cell**